# Examples

In [18]:
import os

if not os.path.basename(os.getcwd()) == "ThousandSuns":
    os.chdir("..")  # Run Once!
%load_ext autoreload
%autoreload 2

from df_objects.df_objects import *
from output_graphs.hourly_graph_creator import *
from scenario_evaluator.run_senarios import *
from hourly_simulation.predict_demand import predict_demand_in_year
from hourly_simulation.parameters import simulation_params, NORMALISED_SOLAR_PRODUCTION
from tests.sanity_checks import test_simulation
import logging

logging.getLogger().setLevel(logging.INFO)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Daily Constant demand different production profiles

In [19]:

num_batteries = 1
print("*Under production*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [9] * 24}))
electricity_use: ElectricityUseDf = strategies.greedy_use_strategy(
    demand=future_demand, production=total_panel_production, params=simulation_params,
    battery_capacity=num_batteries * simulation_params.BATTERY_CAPACITY,
    battery_power=num_batteries * simulation_params.CHARGE_POWER)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)
daily_graph(electricity_use.df)

print("*Over production*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [11] * 24}))
electricity_use: ElectricityUseDf = strategies.greedy_use_strategy(
    demand=future_demand, production=total_panel_production, params=simulation_params,
    battery_capacity=num_batteries * simulation_params.BATTERY_CAPACITY,
    battery_power=num_batteries * simulation_params.CHARGE_POWER)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)
daily_graph(electricity_use.df)

print("*Oscillations around demand*")
future_demand: DemandDf = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                 "Demand": [10] * 24}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(80, 104)],
                                                                  "SolarProduction": [10 + 2 * np.sin(2 * np.pi * x / 6)
                                                                                      for x in range(24)]}))
electricity_use: ElectricityUseDf = strategies.greedy_use_strategy(
    demand=future_demand, production=total_panel_production, params=simulation_params,
    battery_capacity=num_batteries * simulation_params.BATTERY_CAPACITY,
    battery_power=num_batteries * simulation_params.CHARGE_POWER)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)
daily_graph(electricity_use.df)


*Under production*


INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:passed test_charge_power_not_passed
INFO:root:Passed all tests


INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:passed test_charge_power_not_passed
INFO:root:Passed all tests


*Over production*


*Oscillations around demand*


INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:passed test_charge_power_not_passed
INFO:root:Passed all tests


## Yearly Constant demand and sinus production around demand

In [20]:
num_batteries = 1
future_demand = DemandDf(pd.DataFrame({"HourOfYear": [i for i in range(8760)],
                                       "Demand": [10] * 8760}))
total_panel_production: ProductionDf = ProductionDf(pd.DataFrame({"HourOfYear": [i for i in range(8760)],
                                                                  "SolarProduction": [10 + 2 * np.sin(2 * np.pi * x / 6)
                                                                                      for x in range(8760)]}))
electricity_use: ElectricityUseDf = strategies.greedy_use_strategy(
    demand=future_demand, production=total_panel_production, params=simulation_params,
    battery_capacity=num_batteries * simulation_params.BATTERY_CAPACITY,
    battery_power=num_batteries * simulation_params.CHARGE_POWER)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)
yearly_graph(electricity_use.df)

INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:passed test_charge_power_not_passed
INFO:root:Passed all tests


In [21]:
num_batteries = 3.447368
solar_panel_power_kw = 6000
demand = DemandDf(pd.read_csv(r'data/consumption_hatzor.csv', index_col=0))
future_demand = predict_demand_in_year(demand, params=simulation_params, simulated_year=2020)
total_panel_production = ProductionDf(NORMALISED_SOLAR_PRODUCTION.df.copy())
total_panel_production.df[total_panel_production.SolarProduction] *= solar_panel_power_kw
electricity_use: ElectricityUseDf = strategies.greedy_use_strategy(demand=future_demand,
                                                                   production=total_panel_production,
                                                                   params=simulation_params,
                                                                   battery_capacity=simulation_params.BATTERY_CAPACITY * num_batteries,
                                                                   battery_power=simulation_params.CHARGE_POWER * num_batteries)
test_simulation(electricity_use=electricity_use, demand=future_demand, production=total_panel_production,
                params=simulation_params, num_batteries=num_batteries)
yearly_graph(electricity_use.df, num_hours_to_sum=1)

INFO:root:Passed test_non_negative
INFO:root:Passed test_demand_is_reached
INFO:root:passed test_production_is_used
INFO:root:passed test_all_stored_is_used
INFO:root:passed test_battery_capacity_is_not_passed
INFO:root:passed test_charge_power_not_passed
INFO:root:Passed all tests


In [22]:
from hourly_simulation.simulation import *

solar_panel_power_it = np.linspace(6000, 7000, 20)
num_batteries_it = np.linspace(3, 4, 20)
demand = DemandDf(pd.read_csv(r'data/consumption_hatzor.csv', index_col=0))
single_panel_production = ProductionDf(NORMALISED_SOLAR_PRODUCTION.df.copy())
simulated_year = 2020

simulation_results, best_combination = run_scenarios(demand=demand, single_panel_production=single_panel_production,
                                                     simulated_year=simulated_year,
                                                     solar_panel_power_it=solar_panel_power_it,
                                                     num_batteries_it=num_batteries_it,
                                                     strategy=strategies.greedy_use_strategy,
                                                     params=simulation_params)
print(str(best_combination))

100%|██████████| 20/20 [00:07<00:00,  2.69it/s]

PowerSolar      6.526316e+03
NumBatteries    3.473684e+00
Cost            2.698121e+06
Name: 209, dtype: float64


In [23]:
fig = simulation_graph(simulation_results=simulation_results,
                       solar_panel_power_it=solar_panel_power_it,
                       num_batteries_it=num_batteries_it)
fig.show()

In [24]:
from hourly_simulation.simulation import *

solar_panel_power_it = np.linspace(4500, 5500, 20)
num_batteries_it = np.linspace(2.5, 3.5, 20)
demand = DemandDf(pd.read_csv(r'data/consumption_ramat_david.csv', index_col=0))
single_panel_production = ProductionDf(NORMALISED_SOLAR_PRODUCTION.df.copy())
simulated_year = 2020

simulation_results, best_combination = run_scenarios(demand=demand, single_panel_production=single_panel_production,
                                                     strategy=strategies.greedy_use_strategy,
                                                     simulated_year=simulated_year,
                                                     solar_panel_power_it=solar_panel_power_it,
                                                     num_batteries_it=num_batteries_it, params=simulation_params)
print(str(best_combination))

100%|██████████| 20/20 [00:05<00:00,  3.81it/s]

PowerSolar      5.289474e+03
NumBatteries    3.236842e+00
Cost            2.178729e+06
Name: 314, dtype: float64


In [25]:
fig = simulation_graph(simulation_results=simulation_results,
                       solar_panel_power_it=solar_panel_power_it,
                       num_batteries_it=num_batteries_it)
fig.show()